<a href="https://colab.research.google.com/github/RomanTomz/ab_clustermap/blob/master/abandoned_report.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [194]:
import pandas as pd
import folium
import plotly
import re
import numpy as np
from folium import plugins
from folium.plugins import HeatMap

%load_ext google.colab.data_table


The google.colab.data_table extension is already loaded. To reload it, use:
  %reload_ext google.colab.data_table


In [195]:
df = pd.read_csv('/content/drive/My Drive/Colab Notebooks/Work_LCHS/Abandoned/ab_report.csv', parse_dates=['Date reported'])

In [196]:
df['postcode'] = df['Address'].str.extract(r"(\w{1,2}\d{1,2}\w{0,1}\s\d\w{2})")

In [197]:
df.columns

Index(['SR', 'Related SR', 'Date attempted/collected',
       'Month attempted/collected', 'Date reported', 'Month reported',
       'Status', 'MSD Reference', 'Reported by', 'Address', 'Bike Category',
       'Classification', 'Number of bikes reported',
       'Number of bikes collected', 'Bike frame number/s collected', 'Month',
       'Collection attempts', 'Appears undamaged ', 'Partially damaged ',
       'Seriously damaged ', 'Bikes remaining', 'Eligible', 'postcode'],
      dtype='object')

In [198]:
df = df[['SR','Date reported','Number of bikes collected','Collection attempts','postcode']]
df.rename(columns={'Date reported':'date_reported','Number of bikes collected':'bikes_collected','Collection attempts':'outcome'}, inplace=True)
df.date_reported = pd.to_datetime(df.date_reported)

In [199]:
df

SR date_reported  ...                               outcome  postcode
0      1914    2017-08-25  ...  Insufficient information - SR closed  SE20 8TS
1      2055    2017-01-09  ...  Insufficient information - SR closed   E11 2AA
2      6952    2018-06-13  ...  Insufficient information - SR closed    E7 0JR
3      7237    2018-06-27  ...  Insufficient information - SR closed   E16 2RL
4      7474    2018-09-07  ...  Insufficient information - SR closed   CR0 7AZ
...     ...           ...  ...                                   ...       ...
5771  20059    2020-09-08  ...  Insufficient information - SR closed  SE13 5HL
5772  20060    2020-09-08  ...  Insufficient information - SR closed  SW13 9RE
5773  20061    2020-09-08  ...  Insufficient information - SR closed   E17 5LW
5774  20063    2020-09-08  ...  Insufficient information - SR closed   SE1 2LY
5775  20064    2020-09-08  ...  Insufficient information - SR closed   TW2 5PA

[5776 rows x 5 columns]

In [200]:
# Load Postcodes data

postcodes = pd.read_csv('/content/drive/My Drive/Colab Notebooks/Data/spatial_data/open_postcode_geo.csv', header=None, usecols=[0, 6, 7, 8])
postcodes.rename(columns={0:'postcode', 6: 'country',7:'lat',8:'long'}, inplace=True)

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2718: DtypeWarning:

Columns (7,8) have mixed types.Specify dtype option on import or set low_memory=False.



In [201]:
postcodes.head()

postcode   country        lat       long
0  AB1 0AA  Scotland  57.101474  -2.242851
1  AB1 0AB  Scotland  57.102554  -2.246308
2  AB1 0AD  Scotland  57.100556  -2.248342
3  AB1 0AE  Scotland  57.084444  -2.255708
4  AB1 0AF  Scotland  57.096656  -2.258102

In [202]:
merged = df.merge(postcodes, how='inner',left_on='postcode',right_on='postcode')
merged.drop('country', axis=1, inplace=True)

In [203]:
merged.head()

SR date_reported  bikes_collected  ...  postcode        lat       long
0  1914    2017-08-25              0.0  ...  SE20 8TS  51.407151  -0.064774
1  2055    2017-01-09              0.0  ...   E11 2AA  51.579656   0.024395
2  6952    2018-06-13              0.0  ...    E7 0JR  51.554552   0.032904
3  7237    2018-06-27              0.0  ...   E16 2RL  51.501100   0.072439
4  7474    2018-09-07              0.0  ...   CR0 7AZ  51.388831  -0.060361

[5 rows x 7 columns]

In [204]:
start = [51.509865, -0.118092]
london = folium.Map(location=start, zoom_start=11)


In [205]:
merged.lat = merged.lat.str.strip('\\N')
merged['long'] = merged['long'].str.strip('\\N')

In [206]:
merged['long'] = merged['long'].apply(pd.to_numeric)
merged['lat'] = merged['lat'].apply(pd.to_numeric)

In [207]:
merged.dropna(how='any', subset=['lat','long'], inplace=True)

In [208]:
loc = merged[['lat', 'long']].values

In [212]:
london.add_child(plugins.MarkerCluster(loc, popups=merged.outcome))
london

In [211]:
london.save(outfile='ab_map.html')